In [44]:
import os
import pandas as pd
import janitor
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib.ticker import MaxNLocator
import math
%matplotlib inline

In [45]:
outdir="WESTERN_CH_scope"

appln = pd.read_csv(f"{outdir}/tls_201_scope.csv")

appln_title = pd.read_csv(f"{outdir}/tls_202_scope.csv")

pers = pd.read_csv(f"{outdir}/tls_206_scope.csv")

appln_pers = pd.read_csv(f"{outdir}/tls_207_scope.csv")

appln_cpc = pd.read_csv(f"{outdir}/tls_224_scope.csv")

In [46]:
# workdir_path=r"CPCTitleList202302"
# # outfile='wos_extract_complete.csv'
# # with_header=True
# cpc_ids = pd.DataFrame()
# for root, dirs, files in os.walk(workdir_path):
#     for filename in files:
#         path=os.path.join(root, filename)
#         section = pd.read_csv(path, sep='\t', header=None)
#         cpc_ids=pd.concat([cpc_ids,section], ignore_index=True)
# cpc_ids.columns =["cpc_id","idk","cpc_name"]
# cpc_ids = cpc_ids.drop(columns="idk")

In [47]:
parsed = {x: [] for x in ['code', 'title', 'section', 'class', 'subclass', 'group', 'main_group']}
for letter in 'ABCDEFGHY':
    file = f'CPC_data/CPCTitleList202302/cpc-section-{letter}_20230201.txt'
    with open(file) as f:
        for line in f:
            vals = line.strip().split('\t')
            if len(vals) == 2:
                parsed['code'].append(vals[0])
                parsed['title'].append(vals[1])
            elif len(vals) == 3:
                parsed['code'].append(vals[0])
                parsed['title'].append(vals[2])



for i in range(len(parsed['code'])):
    code = parsed['code'][i]
    main_group = code.split('/')[-1] if "/" in code else None
    group = code.split('/')[0][4:] if len(code) >= 5 else None
    subclass = code[3] if len(code) >= 4 else None
    class_ = code[1:3] if len(code) >= 3 else None
    section = code[0] if len(code) >= 1 else None
    
    parsed['main_group'].append(main_group)
    parsed['group'].append(group)
    parsed['subclass'].append(subclass)
    parsed['class'].append(class_)
    parsed['section'].append(section)

cpc_ids2023 = pd.DataFrame.from_dict(parsed)
cpc_ids2023['cpc_version']=2023
cpc_ids2022 = pd.read_csv("CPC_data/cpc_titles_2022.csv")
cpc_ids2022['cpc_version']=2022
cpc_ids = pd.concat([cpc_ids2023,cpc_ids2022], ignore_index=True)
cpc_ids = cpc_ids.rename(columns={"code":"cpc_id","title":"cpc_name"}).drop_duplicates(subset="cpc_id")

In [48]:
appln_cpc["cpc_id"] = appln_cpc["cpc_class_symbol"].str.replace(" ","")
appln_cpc_tax = appln_cpc.merge(cpc_ids, on="cpc_id", how="left")

print(len(appln_cpc_tax[appln_cpc_tax["cpc_name"].isna()]["cpc_id"].unique()), "cpc_ids not found")
print(len(appln_cpc_tax[appln_cpc_tax["cpc_name"].isna()]["cpc_id"].unique())/len(appln_cpc_tax["cpc_id"].unique())*100, "% lost")

70 cpc_ids not found
0.07344840249724569 % lost


In [49]:
cpc_dict = dict(zip(cpc_ids.cpc_id.str.replace(" ",""), cpc_ids.cpc_name))
# cpc_dict

In [50]:
def cpc_classifier(id_text):
    taxonomy = []
    iter_text = id_text.replace(" ","")
    for i in range(len(iter_text)+1):
        tax_id = iter_text[:i]
        tax_name = cpc_dict.get(iter_text[:i])
        if tax_name:
            taxonomy.append((tax_id,tax_name))
    return taxonomy
        

In [51]:
cpc_classifier("A01B1/065")

[('A', 'HUMAN NECESSITIES'),
 ('A01',
  'AGRICULTURE; FORESTRY; ANIMAL HUSBANDRY; HUNTING; TRAPPING; FISHING'),
 ('A01B',
  'SOIL WORKING IN AGRICULTURE OR FORESTRY; PARTS, DETAILS, OR ACCESSORIES OF AGRICULTURAL MACHINES OR IMPLEMENTS, IN GENERAL (making or covering furrows or holes for sowing, planting, or manuring A01C5/00; soil working for engineering purposes E01, E02, E21; {measuring areas for agricultural purposes G01B})'),
 ('A01B1/06',
  'Hoes; Hand cultivators {(rakes A01D7/00; forks A01D9/00; picks B25D)}'),
 ('A01B1/065', '{powered}')]

In [52]:
cpc_ids["cpc_taxonomy"] = cpc_ids["cpc_id"].fillna("").map(cpc_classifier)
cpc_ids.head()


cpc_id                                           cpc_name section class   
0         A                                  HUMAN NECESSITIES       A  None  \
1       A01  AGRICULTURE; FORESTRY; ANIMAL HUSBANDRY; HUNTI...       A    01   
2      A01B  SOIL WORKING IN AGRICULTURE OR FORESTRY; PARTS...       A    01   
3  A01B1/00  Hand tools (edge trimmers for lawns A01G3/06  ...       A    01   
4  A01B1/02  Spades; Shovels {(hand-operated dredgers E02F3...       A    01   

  subclass group main_group  cpc_version   
0     None  None       None         2023  \
1     None  None       None         2023   
2        B  None       None         2023   
3        B     1         00         2023   
4        B     1         02         2023   

  version https://git-lfs.github.com/spec/v1   
0                                        NaN  \
1                                        NaN   
2                                        NaN   
3                                        NaN   
4                                        NaN   

                                        cpc_taxonomy  
0                           [(A, HUMAN NECESSITIES)]  
1  [(A, HUMAN NECESSITIES), (A01, AGRICULTURE; FO...  
2  [(A, HUMAN NECESSITIES), (A01, AGRICULTURE; FO...  
3  [(A, HUMAN NECESSITIES), (A01, AGRICULTURE; FO...  
4  [(A, HUMAN NECESSITIES), (A01, AGRICULTURE; FO...

In [53]:
appln_cpc["cpc_id"] = appln_cpc["cpc_class_symbol"].str.replace(" ","")
appln_cpc_tax = appln_cpc.merge(cpc_ids, on="cpc_id", how="left")
print(len(appln_cpc_tax[appln_cpc_tax["cpc_name"].isna()]["cpc_id"].unique()), "cpc_ids not found")
print(len(appln_cpc_tax[appln_cpc_tax["cpc_name"].isna()]["cpc_id"].unique())/len(appln_cpc_tax["cpc_id"].unique())*100, "% lost")

70 cpc_ids not found
0.07344840249724569 % lost


In [54]:
# cpc_ids
cpc_ids["cpc_fullname"] = cpc_ids["cpc_taxonomy"].apply(lambda x: "<>".join([y[1] for y in x]))
cpc_ids.sample(100)
colnames = ["tax_level_"+ str(i) for i in cpc_ids["cpc_fullname"].str.split('<>', expand=True).columns]
cpc_ids[colnames] = cpc_ids["cpc_fullname"].str.split('<>', expand=True)
# cpc_ids

## 'AI/Big Data' keywords

In [55]:
keywords_oklist_source= r'..\WOS\kw_token_ranked_bibliometrics_okset.xlsx'
keyword_df = pd.read_excel(keywords_oklist_source)
keywords = keyword_df[keyword_df["u_Priority (done)"].isin(["High","Medium"])]["kw_token"].str.replace('"','').tolist()
keywords = [kw.replace("*","").replace("$","").lower() for kw in keywords if ("?" not in kw and len(kw)>3)]
keywords = "|".join([kw for kw in keywords if kw not in ["classifier","clustering","loss function",'classification']]+["relational database"])
keywords

'neural network|machine learn|deep learn|remote sensing|convolutional neural|internet of things|feature extraction|genetic algorithm|big data|artificial intelligence|data driven|support vector machine|logistic regression not p=|optimization algorithm|principal component analysis|artificial neural network|swarm optimization|regularization|linear regression not p=|optimization algorithm|random forest|cloud computing|reinforcement learning|computer vision|kalman filter|image processing|data mining|evolutionary algorithm|edge computing|supervised learning|computational modeling|pattern recognition|image classification|long short-term memor|robotics|image segmentation|convex optimization|covariance matri|attention mechanism|markov chain|object detection not brain|clustering algorithm|recurrent neural network|data augmentation|transfer learning|adversarial network|decision tree|multi agent system|fuzzy set|convolutional network|image reconstruction|data analytic|smart grid|autoencoder|fuzzy 

In [56]:
#dummy search
scope_df = cpc_ids[cpc_ids["cpc_name"].str.lower().str.contains("machine learn|neural network|deep learn|deep network|artificial intel*| big data|database|recommender system|computer vision|image processing|language model|language processing|fuzzy logic|principal component|image classification|video classification", regex=True, na=False)]
scope_df

cpc_id                                           cpc_name   
12725    A61B1/000096                    {using artificial intelligence}  \
13764      A61B5/7264  {Classification of physiological signals or da...   
13897        A61B6/52  {Devices using data or image processing specia...   
14016        A61B8/52  {Devices using data or image processing specia...   
15252   A61B2018/0069                                {using fuzzy logic}   
...               ...                                                ...   
250685  Y10S707/99946         Object-oriented database structure network   
250686  Y10S707/99947       Object-oriented database structure reference   
250687  Y10S707/99948  Application of database or data structure, e.g...   
250688  Y10S707/99951                       File or database maintenance   
250703    Y10S715/968      interface for database querying and retrieval   

       section class subclass group main_group  cpc_version   
12725        A    61        B     1     000096         2023  \
13764        A    61        B     5       7264         2023   
13897        A    61        B     6         52         2023   
14016        A    61        B     8         52         2023   
15252        A    61        B  2018       0069         2023   
...        ...   ...      ...   ...        ...          ...   
250685       Y    10        S   707      99946         2023   
250686       Y    10        S   707      99947         2023   
250687       Y    10        S   707      99948         2023   
250688       Y    10        S   707      99951         2023   
250703       Y    10        S   715        968         2023   

       version https://git-lfs.github.com/spec/v1   
12725                                         NaN  \
13764                                         NaN   
13897                                         NaN   
14016                                         NaN   
15252                                         NaN   
...                                           ...   
250685                                        NaN   
250686                                        NaN   
250687                                        NaN   
250688                                        NaN   
250703                                        NaN   

                                             cpc_taxonomy   
12725   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...  \
13764   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...   
13897   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...   
14016   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...   
15252   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...   
...                                                   ...   
250685  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   
250686  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   
250687  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   
250688  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   
250703  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   

                                             cpc_fullname   
12725   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...  \
13764   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...   
13897   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...   
14016   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...   
15252   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...   
...                                                   ...   
250685  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   
250686  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   
250687  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   
250688  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   
250703  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   

                                              tax_level_0   
12725                                   HUMAN NECESSITIES  \
13764                                   HUMAN NECESSITIES   
13897                                   HUMAN NECESSITIES  

In [57]:
#wos keyword search
scope_df = cpc_ids[cpc_ids["cpc_name"].str.lower().str.contains(keywords, regex=True, na=False)]
scope_df

cpc_id                                           cpc_name   
12725   A61B1/000096                    {using artificial intelligence}  \
13746       A61B5/72  {Signal processing specially adapted for physi...   
13764     A61B5/7264  {Classification of physiological signals or da...   
13897       A61B6/52  {Devices using data or image processing specia...   
14016       A61B8/52  {Devices using data or image processing specia...   
...              ...                                                ...   
246159   Y10S128/924                      using artificial intelligence   
246160   Y10S128/925                                     Neural network   
248454   Y10S323/909                                     Remote sensing   
250570    Y10S706/00           Data processing: artificial intelligence   
250571    Y10S706/90                                        Fuzzy logic   

       section class subclass group main_group  cpc_version   
12725        A    61        B     1     000096         2023  \
13746        A    61        B     5         72         2023   
13764        A    61        B     5       7264         2023   
13897        A    61        B     6         52         2023   
14016        A    61        B     8         52         2023   
...        ...   ...      ...   ...        ...          ...   
246159       Y    10        S   128        924         2023   
246160       Y    10        S   128        925         2023   
248454       Y    10        S   323        909         2023   
250570       Y    10        S   706         00         2023   
250571       Y    10        S   706         90         2023   

       version https://git-lfs.github.com/spec/v1   
12725                                         NaN  \
13746                                         NaN   
13764                                         NaN   
13897                                         NaN   
14016                                         NaN   
...                                           ...   
246159                                        NaN   
246160                                        NaN   
248454                                        NaN   
250570                                        NaN   
250571                                        NaN   

                                             cpc_taxonomy   
12725   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...  \
13746   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...   
13764   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...   
13897   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...   
14016   [(A, HUMAN NECESSITIES), (A61, MEDICAL OR VETE...   
...                                                   ...   
246159  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   
246160  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   
248454  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   
250570  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   
250571  [(Y, GENERAL TAGGING OF NEW TECHNOLOGICAL DEVE...   

                                             cpc_fullname   
12725   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...  \
13746   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...   
13764   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...   
13897   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...   
14016   HUMAN NECESSITIES<>MEDICAL OR VETERINARY SCIEN...   
...                                                   ...   
246159  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   
246160  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   
248454  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   
250570  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   
250571  GENERAL TAGGING OF NEW TECHNOLOGICAL DEVELOPME...   

                                              tax_level_0   
12725                                   HUMAN NECESSITIES  \
13746                                   HUMAN NECESSITIES   
13764                                   HUMAN NECESSITIES   
13897    

In [58]:
scope_ids = scope_df["cpc_id"].unique()
cpc_ids["data_scope"] = cpc_ids["cpc_id"].isin(scope_ids)
cpc_ids.dropna(axis=1, how='all')
cpc_ids.to_csv(f"CPC_data/cpc_defs.csv", index=False)

In [59]:
# cpc_ids

In [60]:
# appln_data = appln.merge(appln_title, on="appln_id")
# appln_data.head()